In [ ]:
#DONT DELETE
import numpy as np
import pandas as pd
import cv2
import os
from scipy.fftpack import dct

from google.colab import drive

# Mount Google Drive
drive.mount('/content/drive')

# Function to compute DCT features from an image window
def compute_dct_features(window, num_features=50):
    if len(window.shape) == 3:
        window = cv2.cvtColor(window, cv2.COLOR_BGR2GRAY)

    window_flat = window.flatten()
    dct_features = dct(window_flat, norm='ortho')[:num_features]
    return dct_features

# Load data from the Excel file
labels_df = pd.read_excel(r'/content/drive/MyDrive/Colab Notebooks/gt_WIndow.xlsx')

# Replace NaN in the Label column with "unknown"
labels_df['Label'] = labels_df['Label'].fillna("unknown")

# Parameters
window_width = 30
step_size = 10
image_folder = r'/content/drive/MyDrive/Colab Notebooks/color_window_double1 (1) 9/color_window_double1 (1)/color_window_double1'

# Dictionary to store DCT feature sequences
character_dct_sequences = {}

for index, row in labels_df.iterrows():
    image_name = row['image name']
    character_sequence = row['Label']

    # Ensure character_sequence is a string
    if not isinstance(character_sequence, str):
        character_sequence = str(character_sequence)

    # Load the corresponding image
    image_path = os.path.join(image_folder, image_name)
    image = cv2.imread(image_path)
    if image is None:
        print(f"Image {image_name} could not be loaded.")
        continue

    image_width = image.shape[1]
    num_characters = len(character_sequence)
    character_width = image_width // num_characters

    for i, char in enumerate(character_sequence):
        region_start = i * character_width
        region_end = region_start + character_width
        character_region = image[:, region_start:region_end]

        num_windows = (character_width - window_width) // step_size + 1
        char_dct_sequence = []

        for j in range(num_windows):
            window_start = region_start + j * step_size
            window_end = window_start + window_width
            window = image[:, window_start:window_end]
            dct_features = compute_dct_features(window)
            char_dct_sequence.append(dct_features)

        if char not in character_dct_sequences:
            character_dct_sequences[char] = []
        character_dct_sequences[char].append(char_dct_sequence)

for char, sequences in character_dct_sequences.items():
    print(f"Character '{char}' has {len(sequences)} sequences of DCT features.")


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Character 'െ' has 618 sequences of DCT features.
Character 'ത' has 535 sequences of DCT features.
Character ' ' has 3720 sequences of DCT features.
Character 'അ' has 103 sequences of DCT features.
Character '്' has 1202 sequences of DCT features.
Character 'ാ' has 993 sequences of DCT features.
Character 'ി' has 729 sequences of DCT features.
Character 'പ' has 339 sequences of DCT features.
Character 'റ' has 432 sequences of DCT features.
Character 'ര' has 681 sequences of DCT features.
Character 'ു' has 455 sequences of DCT features.
Character 'ള' has 78 sequences of DCT features.
Character 'ക' has 473 sequences of DCT features.
Character 'ഷ' has 105 sequences of DCT features.
Character 'മ' has 361 sequences of DCT features.
Character 'ആ' has 28 sequences of DCT features.
Character 'ഠ' has 61 sequences of DCT features.
Character 'ൽ' has 40 sequences of DCT f

In [ ]:
!pip install hmmlearn

import numpy as np
from hmmlearn import hmm

# Dictionary to store character HMMs
character_hmms = {}
num_states=4
# Example: 'character_dct_sequences' contains the DCT feature sequences for each character
for char, sequences in character_dct_sequences.items():
    # Remove empty sequences
    sequences = [seq for seq in sequences if len(seq) > 0]

    if len(sequences) == 0:
        print(f"Warning: No valid sequences for character {char}. Skipping this character.")
        continue  # Skip to the next character if no valid sequences
    if len(sequences) >=15:
    # Prepare training data for the HMM
        X = np.vstack(sequences)  # Stack the sequences into a single array
        lengths = [len(seq) for seq in sequences]  # Length of each sequence

        # Initialize HMM for this character
        model = hmm.GaussianHMM(n_components=num_states, covariance_type="diag", n_iter=1000)

        # Train the HMM with the character’s DCT feature sequences
        model.fit(X, lengths)

        # Store the trained model
        character_hmms[char] = model
        print(f"Model trained for character: {char}")


Model trained for character: െ
Model trained for character: ത
Model trained for character:  
Model trained for character: അ
Model trained for character: ്
Model trained for character: ാ
Model trained for character: ി
Model trained for character: പ
Model trained for character: റ
Model trained for character: ര
Model trained for character: ു
Model trained for character: ള
Model trained for character: ക
Model trained for character: ഷ
Model trained for character: മ
Model trained for character: ആ
Model trained for character: ഠ
Model trained for character: ൽ
Model trained for character: ർ
Model trained for character: ഇ
Model trained for character: ങ
Model trained for character: ന
Model trained for character: ജ
Model trained for character: ട
Model trained for character: വ
Model trained for character: ഹ
Model trained for character: ം
Model trained for character: യ
Model trained for character: u
Model trained for character: n
Model trained for character: k
Model trained for character: o
Model tr

In [ ]:
import joblib
import re
import os
from zipfile import ZipFile
from google.colab import files  # Ensure the correct module is imported

# Assuming your models are in a dictionary called `character_hmms`
# Example: character_hmms = {'െ': trained_model_1, 'ത': trained_model_2, ... }

def sanitize_filename(char):
    """Replace invalid filename characters with an underscore."""
    return re.sub(r'[<>:"/\\|?*]', '_', char)

# Create a directory to save the models
output_dir = "saved_models"
os.makedirs(output_dir, exist_ok=True)

# Save each model with a sanitized filename
for char, model in character_hmms.items():
    sanitized_char = sanitize_filename(char)
    file_path = os.path.join(output_dir, f"{sanitized_char}_hmm.pkl")
    joblib.dump(model, file_path)
    print(f"Model for character '{char}' saved as '{file_path}'.")

# Compress all saved models into a ZIP file
zip_filename = "models.zip"
with ZipFile(zip_filename, 'w') as zipf:
    for root, dirs, files_in_dir in os.walk(output_dir):
        for file in files_in_dir:
            zipf.write(os.path.join(root, file), os.path.relpath(os.path.join(root, file), output_dir))

print(f"All models are zipped into '{zip_filename}'.")

# Download the ZIP file in Colab
files.download(zip_filename)


Model for character 'െ' saved as 'saved_models/െ_hmm.pkl'.
Model for character 'ത' saved as 'saved_models/ത_hmm.pkl'.
Model for character ' ' saved as 'saved_models/ _hmm.pkl'.
Model for character 'അ' saved as 'saved_models/അ_hmm.pkl'.
Model for character '്' saved as 'saved_models/്_hmm.pkl'.
Model for character 'ാ' saved as 'saved_models/ാ_hmm.pkl'.
Model for character 'ി' saved as 'saved_models/ി_hmm.pkl'.
Model for character 'പ' saved as 'saved_models/പ_hmm.pkl'.
Model for character 'റ' saved as 'saved_models/റ_hmm.pkl'.
Model for character 'ര' saved as 'saved_models/ര_hmm.pkl'.
Model for character 'ു' saved as 'saved_models/ു_hmm.pkl'.
Model for character 'ള' saved as 'saved_models/ള_hmm.pkl'.
Model for character 'ക' saved as 'saved_models/ക_hmm.pkl'.
Model for character 'ഷ' saved as 'saved_models/ഷ_hmm.pkl'.
Model for character 'മ' saved as 'saved_models/മ_hmm.pkl'.
Model for character 'ആ' saved as 'saved_models/ആ_hmm.pkl'.
Model for character 'ഠ' saved as 'saved_models/ഠ_hmm.pkl

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
# Extract the character names (keys) from the character_hmms dictionary
char_names = list(character_hmms.keys())

# Print the character names
print("Character names:", char_names)


Character names: ['െ', 'ത', ' ', 'അ', '്', 'ാ', 'ി', 'പ', 'റ', 'ര', 'ു', 'ള', 'ക', 'ഷ', 'മ', 'ആ', 'ഠ', 'ൽ', 'ർ', 'ഇ', 'ങ', 'ന', 'ജ', 'ട', 'വ', 'ഹ', 'ം', 'യ', 'u', 'n', 'k', 'o', 'w', 'ധ', 'ച', 'എ', 'ല', 'ഴ', 'ദ', 'ഗ', 'ഉ', 'ണ', 'ൂ', 'ൻ', 'സ', 'ീ', 'ഭ', 'ഖ', 'ശ', 'ൈ', 'ഥ', 'ൾ', 'ഘ', 'ൃ', 'ൊ', 'ഞ', 'ബ', 'ഃ', '\xa0']


In [ ]:
ground_truth =char_names

In [ ]:
unique_chars = sorted(set("".join(ground_truth)))
char_to_state = {char: idx for idx, char in enumerate(unique_chars)}
state_to_char = {idx: char for char, idx in char_to_state.items()}

In [ ]:
from nltk.translate.bleu_score import sentence_bleu
import numpy as np

# Calculate BLEU score for predictions (this is more useful for sequence generation tasks)
for char, model in character_hmms.items():
    sequences = character_dct_sequences[char]

    # Remove empty sequences
    sequences = [seq for seq in sequences if len(seq) > 0]

    # Check if we have any sequences left
    if len(sequences) >=15:

        X = np.vstack(sequences)


    lengths = [len(seq) for seq in sequences]

    # Get predicted states
    predicted_states = model.predict(X)
    mapped_predictions = [state_to_char[state] for state in predicted_states]

# Calculate BLEU score
bleu_score = sentence_bleu([ground_truth], mapped_predictions)
print(f"BLEU Score: {bleu_score}")


BLEU Score: 5.259175947622844e-232


/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_

In [ ]:
import pandas as pd
import numpy as np

# Read line sequences from Excel

# Assuming the line sequences are in a column named 'line_sequence' or similar
line_sequences = labels_df['Label'].tolist()

# Example line sequence (you can iterate through all lines in your dataset)
# line_sequence = ['ര', 'വ', 'ി', 'ട', 'ു']  # Example line sequence


In [ ]:
# Get indices for each individual character, but skip characters not in char_to_index
line_sequence_indices = [char_to_state [individual_char]
                         for char_group in line_sequences
                         for individual_char in char_group
                         if individual_char in char_to_state ]
print("Line sequence indices:", line_sequence_indices)

Line sequence indices: [51, 25, 51, 0, 9, 25, 54, 25, 0, 25, 45, 0, 46, 30, 0, 30, 0, 36, 0, 35, 48, 0, 35, 38, 0, 45, 38, 0, 14, 0, 51, 51, 42, 0, 33, 45, 0, 46, 25, 54, 25, 46, 25, 54, 25, 46, 10, 0, 25, 54, 35, 0, 51, 51, 23, 0, 14, 0, 14, 0, 45, 57, 0, 57, 0, 56, 0, 11, 11, 0, 11, 0, 51, 45, 0, 51, 14, 51, 0, 18, 54, 14, 0, 18, 54, 14, 0, 45, 0, 51, 51, 29, 51, 0, 29, 0, 36, 0, 51, 51, 20, 51, 0, 14, 36, 0, 14, 22, 54, 35, 0, 22, 54, 35, 46, 0, 22, 54, 35, 46, 0, 22, 0, 22, 54, 22, 48, 0, 22, 54, 22, 48, 0, 23, 0, 48, 23, 0, 23, 0, 40, 0, 44, 0, 44, 36, 0, 46, 35, 46, 0, 35, 46, 0, 51, 25, 51, 0, 25, 0, 25, 7, 0, 51, 29, 51, 0, 29, 54, 29, 0, 29, 7, 0, 34, 0, 34, 0, 34, 51, 0, 34, 0, 34, 0, 45, 46, 0, 45, 45, 4, 2, 1, 2, 3, 5, 2, 30, 0, 30, 0, 14, 0, 10, 0, 10, 0, 28, 46, 0, 19, 54, 19, 46, 19, 54, 19, 0, 19, 54, 19, 0, 19, 0, 46, 0, 51, 36, 51, 0, 25, 0, 25, 0, 29, 54, 0, 29, 54, 29, 46, 0, 29, 54, 29, 46, 0, 36, 46, 0, 22, 54, 22, 48, 0, 22, 54, 22, 48, 0, 36, 0, 9, 0, 9, 0, 38, 

In [ ]:
# Mount Google Drive
from google.colab import drive
import joblib
from hmmlearn import hmm
import cv2
import os

# Mount the drive
drive.mount('/content/drive')

# Define the path to the folder containing HMM models
hmm_model_folder = '/content/drive/MyDrive/Colab Notebooks/models'


# Dynamically load character HMM models
character_hmms = {}

# Iterate over all .pkl files in the HMM models folder
for filename in os.listdir(hmm_model_folder):
    if filename.endswith('_hmm.pkl'):
        char = filename.split('_hmm.pkl')[0]  # Extract the character name
        model_path = os.path.join(hmm_model_folder, filename)
        try:
            model = joblib.load(model_path)  # Load the model
            character_hmms[char] = model
        except Exception as e:
            print(f"Failed to load model for '{char}': {e}")

print(f"Loaded HMM models for characters: {list(character_hmms.keys())}")

# Function to compute DCT features (ensure this is implemented elsewhere)
def compute_dct_features(image_window):
    # Placeholder for DCT feature computation
    import numpy as np
    from scipy.fftpack import dct
    flattened = image_window.flatten()
    return dct(flattened, norm='ortho')

# Function to predict line sequence based on HMMs
def predict_line_sequence(line_image, window_width=30, step_size=10):
    predictions = []
    image_width = line_image.shape[1]
    num_windows = (image_width - window_width) // step_size + 1

    for i in range(num_windows):
        window_start = i * step_size
        window_end = window_start + window_width
        window = line_image[:, window_start:window_end]

        # Compute DCT features for the window
        dct_features = compute_dct_features(window)
        dct_features = dct_features.reshape(1, -1)

        # Calculate likelihoods for each character model
        best_char = None
        best_score = float('-inf')

        for char, model in character_hmms.items():
            try:
                score = model.score(dct_features)
                if score > best_score:
                    best_score = score
                    best_char = char
            except:
                pass  # Ignore errors for invalid model scoring

        if best_char is not None:
            predictions.append(best_char)

    return ''.join(predictions)

# Load a test line image
test_image_path = '/content/drive/MyDrive/Colab Notebooks/color_window_double1 (1) 9/color_window_double1 (1)/color_window_double1/mal286_010_9.jpg_window_38.jpg'
test_image = cv2.imread(test_image_path, cv2.IMREAD_GRAYSCALE)

if test_image is None:
    raise ValueError(f"Failed to load the test image from: {test_image_path}")

# Predict the character sequence in the test line image
predicted_sequence = predict_line_sequence(test_image)
print("Predicted line sequence:", predicted_sequence)


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Loaded HMM models for characters: ['ട', 'ണ', 'ഞ', 'ഥ', 'ത', 'ഠ', 'ധ', 'ദ', 'ജ', 'ഘ', 'എ', 'ഉ', 'ച', 'ക', 'ഖ', 'ഗ', 'ഇ', 'ങ', 'അ', 'ആ', 'u', 'k', 'o', '', 'n', 'w', 'ം', 'ഃ', 'െ', 'ൻ', 'ൽ', 'ൃ', 'ൂ', 'ഹ', 'ഷ', 'ാ', 'ി', 'സ', 'ശ', 'ു', 'ീ', 'വ', 'ള', 'ഴ', 'യ', 'ര', 'മ', 'റ', 'ഭ', 'ബ', 'ല', 'പ', 'ന', '്', 'ൾ', 'ർ', 'ൈ', 'ൊ']
Predicted line sequence: 


In [ ]:
# Mount Google Drive
from google.colab import drive
import joblib
from hmmlearn import hmm
import cv2
import os

#Mount the drive
drive.mount('/content/drive')

# Define the path to the folder containing HMM models
hmm_model_folder = '/content/drive/MyDrive/Colab Notebooks/models'


#Dynamically load character HMM models
character_hmms = {}

#Iterate over all .pkl files in the HMM models folder
for filename in os.listdir(hmm_model_folder):
    if filename.endswith('_hmm.pkl'):
        char = filename.split('_hmm.pkl')[0]  # Extract the character name
        model_path = os.path.join(hmm_model_folder, filename)
        try:
            model = joblib.load(model_path)  # Load the model
            character_hmms[char] = model
        except Exception as e:
            print(f"Failed to load model for '{char}': {e}")

print(f"Loaded HMM models for characters: {list(character_hmms.keys())}")

# Function to compute DCT features (ensure this is implemented elsewhere)
def compute_dct_features(window, num_features=50):
    if len(window.shape) == 3:
        window = cv2.cvtColor(window, cv2.COLOR_BGR2GRAY)

    window_flat = window.flatten()
    dct_features = dct(window_flat, norm='ortho')[:num_features]
    return dct_features


# Function to predict line sequence based on HMMs
def predict_line_sequence(line_image, window_width=30, step_size=10):
    predictions = []
    image_width = line_image.shape[1]
    num_windows = (image_width - window_width) // step_size + 1

    for i in range(num_windows):
        window_start = i * step_size
        window_end = window_start + window_width
        window = line_image[:, window_start:window_end]

        # Compute DCT features for the window
        dct_features = compute_dct_features(window)
        dct_features = dct_features.reshape(1, -1)

        # Calculate likelihoods for each character model
        best_char = None
        best_score = float('-inf')

        for char, model in character_hmms.items():
            try:
                score = model.score(dct_features)
                if score > best_score:
                    best_score = score
                    best_char = char
            except:
                pass  # Ignore errors for invalid model scoring

        if best_char is not None:
            predictions.append(best_char)

    return ''.join(predictions)

# Load a test line image
test_image_path = r'/content/drive/MyDrive/Colab Notebooks/color_window_double1 (1) 9/color_window_double1 (1)/color_window_double1/mal286_010_9.jpg_window_38.jpg'
test_image = cv2.imread(test_image_path, cv2.IMREAD_GRAYSCALE)

if test_image is None:
    raise ValueError(f"Failed to load the test image from: {test_image_path}")

# Predict the character sequence in the test line image
predicted_sequence = predict_line_sequence(test_image)
print("Predicted line sequence:", predicted_sequence)


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Loaded HMM models for characters: ['ട', 'ണ', 'ഞ', 'ഥ', 'ത', 'ഠ', 'ധ', 'ദ', 'ജ', 'ഘ', 'എ', 'ഉ', 'ച', 'ക', 'ഖ', 'ഗ', 'ഇ', 'ങ', 'അ', 'ആ', 'u', 'k', 'o', '', 'n', 'w', 'ം', 'ഃ', 'െ', 'ൻ', 'ൽ', 'ൃ', 'ൂ', 'ഹ', 'ഷ', 'ാ', 'ി', 'സ', 'ശ', 'ു', 'ീ', 'വ', 'ള', 'ഴ', 'യ', 'ര', 'മ', 'റ', 'ഭ', 'ബ', 'ല', 'പ', 'ന', '്', 'ൾ', 'ർ', 'ൈ', 'ൊ']
Predicted line sequence: െചൽെണിഥയഥഥഥഥൽൽെപെൽടെചറഠിിെെടെെ


In [ ]:
character_hmms

{'ട': GaussianHMM(n_components=4, n_iter=1000),
 'ണ': GaussianHMM(n_components=4, n_iter=1000),
 'ഞ': GaussianHMM(n_components=4, n_iter=1000),
 'ഥ': GaussianHMM(n_components=4, n_iter=1000),
 'ത': GaussianHMM(n_components=4, n_iter=1000),
 'ഠ': GaussianHMM(n_components=4, n_iter=1000),
 'ധ': GaussianHMM(n_components=4, n_iter=1000),
 'ദ': GaussianHMM(n_components=4, n_iter=1000),
 'ജ': GaussianHMM(n_components=4, n_iter=1000),
 'ഘ': GaussianHMM(n_components=4, n_iter=1000),
 'എ': GaussianHMM(n_components=4, n_iter=1000),
 'ഉ': GaussianHMM(n_components=4, n_iter=1000),
 'ച': GaussianHMM(n_components=4, n_iter=1000),
 'ക': GaussianHMM(n_components=4, n_iter=1000),
 'ഖ': GaussianHMM(n_components=4, n_iter=1000),
 'ഗ': GaussianHMM(n_components=4, n_iter=1000),
 'ഇ': GaussianHMM(n_components=4, n_iter=1000),
 'ങ': GaussianHMM(n_components=4, n_iter=1000),
 'അ': GaussianHMM(n_components=4, n_iter=1000),
 'ആ': GaussianHMM(n_components=4, n_iter=1000),
 'u': GaussianHMM(n_components=4, n_iter

In [ ]:
import os
import pandas as pd
import cv2
from nltk.translate.bleu_score import sentence_bleu
from google.colab import files
from scipy.fftpack import dct
# Mount Google Drive
from google.colab import drive
import joblib
from hmmlearn import hmm

#Mount the drive
drive.mount('/content/drive')

# Define the path to the folder containing HMM models
hmm_model_folder = '/content/drive/MyDrive/Colab Notebooks/models'


#Dynamically load character HMM models
character_hmms = {}

#Iterate over all .pkl files in the HMM models folder
for filename in os.listdir(hmm_model_folder):
    if filename.endswith('_hmm.pkl'):
        char = filename.split('_hmm.pkl')[0]  # Extract the character name
        model_path = os.path.join(hmm_model_folder, filename)
        try:
            model = joblib.load(model_path)  # Load the model
            character_hmms[char] = model
        except Exception as e:
            print(f"Failed to load model for '{char}': {e}")

print(f"Loaded HMM models for characters: {list(character_hmms.keys())}")

# Function to compute DCT features (ensure this is implemented elsewhere)
def compute_dct_features(window, num_features=50):
    if len(window.shape) == 3:
        window = cv2.cvtColor(window, cv2.COLOR_BGR2GRAY)

    window_flat = window.flatten()
    dct_features = dct(window_flat, norm='ortho')[:num_features]
    return dct_features


# Function to predict line sequence based on HMMs
def predict_line_sequence(line_image, window_width=30, step_size=10):
    predictions = []
    image_width = line_image.shape[1]
    num_windows = (image_width - window_width) // step_size + 1

    for i in range(num_windows):
        window_start = i * step_size
        window_end = window_start + window_width
        window = line_image[:, window_start:window_end]

        # Compute DCT features for the window
        dct_features = compute_dct_features(window)
        dct_features = dct_features.reshape(1, -1)

        # Calculate likelihoods for each character model
        best_char = None
        best_score = float('-inf')

        for char, model in character_hmms.items():
            try:
                score = model.score(dct_features)
                if score > best_score:
                    best_score = score
                    best_char = char
            except:
                pass  # Ignore errors for invalid model scoring

        if best_char is not None:
            predictions.append(best_char)

    return ''.join(predictions)



# Function to calculate BLEU score
def calculate_bleu_score(actual_sequence, predicted_sequence):
    reference = [list(actual_sequence)]  # Wrap in another list for multiple references
    hypothesis = list(predicted_sequence)
    bleu_score = sentence_bleu(reference, hypothesis)
    return bleu_score

# Function to extract the actual sequence from the DataFrame
def get_actual_sequence_from_df(image_name, line_image, label_df, window_width=50, step_size=5):
    # Find the label for the image from the DataFrame
    label_row = label_df[label_df['image name'] == image_name]

    if label_row.empty:
        print(f"Label not found for image: {image_name}")
        return None

    # Extract the character sequence for the image
    character_sequence = label_row.iloc[0]['Label']

    # Ensure the character_sequence is in string format
    if isinstance(character_sequence, str):
        # If the character sequence is already a string, return it
        return list(character_sequence)
    elif isinstance(character_sequence, float):
        # Handle the case where the character sequence might be incorrectly read as a float
        print(f"Invalid character sequence for image {image_name}: {character_sequence}")
        return None
    else:
        # Handle any unexpected data types
        print(f"Unexpected character sequence data type for image {image_name}")
        return None

# Folder paths and files (Google Drive path)
image_folder = '/content/drive/MyDrive/Colab Notebooks/color_window_double1 (1) 9/color_window_double1 (1)/color_window_double1'
label_file = '/content/drive/MyDrive/Colab Notebooks/gt_WIndow.xlsx'  # Change to correct label file
output_file = '/content/drive/MyDrive/Colab Notebooks/BLEU_Scores.xlsx'

# Load the labels DataFrame
label_df = pd.read_excel(label_file)

# List all image files in the folder
image_files = [f for f in os.listdir(image_folder) if f.endswith(('.jpg', '.png'))]

# Initialize a results list
results = []

# Process each image
for image_name in image_files:
    image_path = os.path.join(image_folder, image_name)

    # Load the image
    image = cv2.imread(image_path, cv2.IMREAD_GRAYSCALE)
    if image is None:
        print(f"Error loading image: {image_name}")
        continue

    # Extract the actual sequence from the DataFrame
    actual_sequence = get_actual_sequence_from_df(image_name, image, label_df)  # Ensure this function works for your case
    if actual_sequence is None:
        print(f"No label found for image: {image_name}")
        continue

    # Predict the sequence using the HMM models
    predicted_sequence = predict_line_sequence(image)  # Ensure this function works for your case

    # Calculate BLEU score
    bleu_score = calculate_bleu_score(actual_sequence, predicted_sequence)

    # Append results
    results.append({
        "Image Name": image_name,
        "Actual Sequence": ''.join(actual_sequence),
        "Predicted Sequence": ''.join(predicted_sequence),
        "BLEU Score": bleu_score
    })

# Save the results to an Excel sheet
results_df = pd.DataFrame(results)
results_df.to_excel(output_file, index=False)

# Download the file
files.download(output_file)

print(f"Results saved to {output_file} and file ready for download.")


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Loaded HMM models for characters: ['', 'ഉ', 'എ', 'ഃ', 'ൈ', 'ണ', 'ധ', 'ര', 'റ', 'ം', 'വ', 'ട', 'ഹ', '്', 'ഗ', 'ജ', 'യ', 'ന', 'ൾ', 'ാ', 'ഞ', 'ക', 'ഥ', 'ആ', 'ർ', 'n', 'ഴ', 'ൂ', 'ു', 'ി', 'ങ', 'ദ', 'ീ', 'ല', 'ൽ', 'അ', 'ഷ', 'ശ', 'o', 'ൃ', 'k', 'െ', 'w', 'ഠ', 'ൊ', 'ള', 'പ', 'മ', 'ത', 'ബ', 'ച', 'ഇ', 'സ', 'u', 'ഭ', 'ഖ', 'ഘ', 'ൻ']
Label not found for image: mal286_010_9.jpg_window_51.jpg
No label found for image: mal286_010_9.jpg_window_51.jpg
Label not found for image: mal286_010_9.jpg_window_44.jpg
No label found for image: mal286_010_9.jpg_window_44.jpg
Label not found for image: mal286_010_9.jpg_window_50.jpg
No label found for image: mal286_010_9.jpg_window_50.jpg


/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_

Invalid character sequence for image MaI849_041_line_4.jpg_window_13.jpg: nan
No label found for image: MaI849_041_line_4.jpg_window_13.jpg
Invalid character sequence for image MaI849_041_line_4.jpg_window_37.jpg: nan
No label found for image: MaI849_041_line_4.jpg_window_37.jpg


/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_

Invalid character sequence for image MaI849_041_line_4.jpg_window_38.jpg: nan
No label found for image: MaI849_041_line_4.jpg_window_38.jpg


...

Invalid character sequence for image MaI12_Page100_line_2.jpg_window_16.jpg: nan
No label found for image: MaI12_Page100_line_2.jpg_window_16.jpg


/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Results saved to /content/drive/MyDrive/Colab Notebooks/BLEU_Scores.xlsx and file ready for download.


In [ ]:
import os
import pandas as pd
from nltk.translate.bleu_score import sentence_bleu
import cv2

# Function to calculate BLEU score
def calculate_bleu_score(actual_sequence, predicted_sequence):
    # Ensure actual_sequence and predicted_sequence are strings or lists
    if not actual_sequence or not predicted_sequence:
        print("Error: One of the sequences is empty.")
        return 0.0
    reference = [list(str(actual_sequence))]  # Convert to list of characters for BLEU calculation
    hypothesis = list(str(predicted_sequence))
    bleu_score = sentence_bleu(reference, hypothesis)
    return bleu_score

# Folder paths and files
image_folder = '/content/drive/MyDrive/Colab Notebooks/color_window_double1 (1) 9/color_window_double1 (1)/color_window_double1'
label_file = '/content/drive/MyDrive/Colab Notebooks/gt_WIndow.xlsx'
output_file = '/content/drive/MyDrive/Colab Notebooks/BLEU_Scores.xlsx'

# Load the labels DataFrame
label_df = pd.read_excel(label_file)

# List all image files in the folder
image_files = [f for f in os.listdir(image_folder) if f.endswith(('.jpg', '.png'))]

# Initialize a results list
results = []

# Function to extract actual sequence from label DataFrame
def get_actual_sequence_from_df(image_name, label_df):
    try:
        row = label_df[label_df['image name'] == image_name]
        if row.empty:
            raise ValueError(f"Image name '{image_name}' not found in the labels DataFrame.")
        return str(row['Label'].values[0])  # Ensure it returns a string
    except ValueError as e:
        print(e)
        return None

# Process each image
for image_name in image_files:
    image_path = os.path.join(image_folder, image_name)

    # Load the image
    image = cv2.imread(image_path, cv2.IMREAD_GRAYSCALE)
    if image is None:
        print(f"Error loading image: {image_name}")
        continue

    # Extract the actual sequence from the DataFrame
    actual_sequence = get_actual_sequence_from_df(image_name, label_df)
    if actual_sequence is None:
        print(f"Skipping image {image_name} due to missing actual sequence.")
        continue

    # Predict the sequence using the HMM models
    predicted_sequence = predict_line_sequence(image)

    # Calculate BLEU score
    try:
        bleu_score = calculate_bleu_score(actual_sequence, predicted_sequence)
    except Exception as e:
        print(f"Error calculating BLEU score for {image_name}: {e}")
        continue

    # Append results
    results.append({
        "Image Name": image_name,
        "Actual Sequence": actual_sequence,
        "Predicted Sequence": predicted_sequence,
        "BLEU Score": bleu_score
    })

# Save the results to an Excel sheet
results_df = pd.DataFrame(results)
results_df.to_excel(output_file, index=False)

print(f"Results saved to {output_file}")


Streaming output truncated to the last 5000 lines.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently 

Image name 'mal286_010_1.jpg_window_17.jpg' not found in the labels DataFrame.
Skipping image mal286_010_1.jpg_window_17.jpg due to missing actual sequence.


/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_

Image name 'mal286_010_1.jpg_window_16.jpg' not found in the labels DataFrame.
Skipping image mal286_010_1.jpg_window_16.jpg due to missing actual sequence.


/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_

...

/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_

Image name 'mal286_010_1.jpg_window_14.jpg' not found in the labels DataFrame.
Skipping image mal286_010_1.jpg_window_14.jpg due to missing actual sequence.


/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_

Image name 'mal286_010_2.jpg_window_16.jpg' not found in the labels DataFrame.
Skipping image mal286_010_2.jpg_window_16.jpg due to missing actual sequence.
Image name 'mal286_010_2.jpg_window_14.jpg' not found in the labels DataFrame.
Skipping image mal286_010_2.jpg_window_14.jpg due to missing actual sequence.
Image name 'mal286_010_1.jpg_window_24.jpg' not found in the labels DataFrame.
Skipping image mal286_010_1.jpg_window_24.jpg due to missing actual sequence.
Image name 'mal286_010_1.jpg_window_49.jpg' not found in the labels DataFrame.
Skipping image mal286_010_1.jpg_window_49.jpg due to missing actual sequence.
Image name 'mal286_010_2.jpg_window_11.jpg' not found in the labels DataFrame.
Skipping image mal286_010_2.jpg_window_11.jpg due to missing actual sequence.
Image name 'mal286_010_1.jpg_window_37.jpg' not found in the labels DataFrame.
Skipping image mal286_010_1.jpg_window_37.jpg due to missing actual sequence.
Image name 'mal286_010_1.jpg_window_42.jpg' not found in t

Streaming output truncated to the last 5000 lines.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently 

In [ ]:
import pandas as pd

# Load the data
file_path = '/content/drive/MyDrive/Colab Notebooks/character_comparison_results_all.xlsx'  # Update this to your file's location in Colab
data = pd.read_excel(file_path)

# Calculate accuracy
accuracy = data['Result'].mean()  # Mean of True (1) and False (0) gives accuracy
print(f"Accuracy: {accuracy * 100:.2f}%")


Accuracy: 16.29%


In [ ]:
# Import necessary libraries
import pandas as pd
from google.colab import drive


#Mount the drive
drive.mount('/content/drive')

# Load the Excel file
file_path = '/content/drive/MyDrive/Colab Notebooks/BLEU_Scores (1).xlsx'  # Update the file path if necessary
data = pd.ExcelFile(file_path)

# Display sheet names
print("Available sheets:", data.sheet_names)

# Load the first sheet (or a specific sheet name if needed)
df = data.parse(data.sheet_names[0])  # Replace '0' with sheet name if necessary
print("Preview of the data:")
print(df.head())

# Assuming the file has 'actual' and 'predicted' columns
# Replace 'actual' and 'predicted' with the correct column names from your dataset
actual_col = "Actual Sequence"  # Replace with the actual column name for true labels
predicted_col = "Predicted Sequence"  # Replace with the column name for predicted labels

# Check if the required columns exist
if actual_col in df.columns and predicted_col in df.columns:
    # Calculate accuracy
    correct_predictions = (df[actual_col] == df[predicted_col]).sum()
    total_predictions = len(df)
    accuracy = correct_predictions / total_predictions

    print(f"Accuracy: {accuracy:.2%}")
else:
    print(f"Columns '{actual_col}' and/or '{predicted_col}' not found in the dataset.")


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Available sheets: ['Sheet1']
Preview of the data:
                            Image Name Actual Sequence  \
0  MaI849_039_line_9.jpg_window_32.jpg              ശെ   
1  MaI849_039_line_9.jpg_window_11.jpg            ആരു    
2  MaI849_039_line_9.jpg_window_29.jpg           ൻ ററ    
3   MaI849_039_line_9.jpg_window_5.jpg           ണ്ടാ    
4  MaI849_039_line_9.jpg_window_33.jpg            ശ ഷ    

               Predicted Sequence     BLEU Score  
0  ണററപൽബബർർീഹണwെകഅശശശശതതഷർസസഷഷwണ  9.257325e-232  
1  ആസആആആആതതഭഴഹഹപമകറഅവശവംചടടആറൈളളഴ  7.784451e-232  
2  ൻൻെർൻശഹൂൃൃാൃറണടകകമദടടഴെറണണണടറൻ  1.024491e-231  
3  ളളളൾൾൾർഴഴംചളശശടൻടീചഴൻnശദkkkkശാ  9.257325e-232  
4  കകഅശശശശശൽഷർസസആഷwണൊwഷംരർചചചചചഷ  9.257325e-232  
Accuracy: 0.00%
